# Madagascar DroneMD (Metadata) Notebook

### Common variables:

In [209]:
# Script folder
dronemdt_folder = '/home/sylvain/DroneMDT'
# Session / Flight data input
input = '/home/sylvain/HDD5To/DATA/MADAGASCAR'
# Output geoflow config (json and csv entities)
output = '/home/sylvain/HDD5To/DATA/MADAGASCAR'
# Geoflow folder where .env is stored and jobs will be available
geoflow_folder = '/home/sylvain/geoflow-g2oi'
# Geoserver configuration
WS = 'IHSM'
DS = 'dronemadagascar'
# Zenodo setup
sandbox = False
# Move to dronemdt_folder
import os
os.chdir(dronemdt_folder)

## Part 1a: Check images validity

In [104]:
# DATA have to be copied from Drone internal storage or sdcard DCIM folder using suh naming convention:
# YYYYMMDD_COUNTRYCODE-optionalplace_device_session-number
# ├── DCIM :  folder to store videos and photos depending on the media collected
#
# Check validity of images copied from Drone to disk
# rclone copy cloudIRD:/G2OI/Missions/Aldabra /media/HDD5To/DATA/ALDABRA/

In [105]:
from check_images import *
img_list = im_list(input)
for i in range(len(img_list)):
    check_image_with_pil(img_list[i])

In [106]:
from check_images import *
img_list = im_list(input)
for i in range(len(img_list)):
    # print(i, img_list[i])
    imgv = Image.open(img_list[i])
    # imgv = check_image_with_pil(img_list[i])
    print(img_list[i], imgv)

/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/00_sample_rawdata_overview.png <PIL.PngImagePlugin.PngImageFile image mode=RGBA size=960x720 at 0x7F70A01C7430>
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/PROCESSED_DATA/PHOTOGRAMMETRY/odm_texturing/odm_textured_model_geo_material0010_map_Kd.png <PIL.PngImagePlugin.PngImageFile image mode=RGB size=8192x8192 at 0x7F6DEF5FA4D0>
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/PROCESSED_DATA/PHOTOGRAMMETRY/odm_texturing/odm_textured_model_geo_material0020_map_Kd.png <PIL.PngImagePlugin.PngImageFile image mode=RGB size=1024x1024 at 0x7F87C69B5900>
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/PROCESSED_DATA/PHOTOGRAMMETRY/odm_texturing/odm_textured_model_geo_material0011_map_Kd.png <PIL.PngImagePlugin.PngImageFile image mode=RGB size=8192x8192 at 0x7F6DEF5FA4D0>
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/PROCESSED_DATA/PHOTOGRAM

IOPub data rate exceeded.
The Jupyter server will temporarily stop sending output
to the client in order to avoid crashing it.
To change this limit, set the config variable
`--ServerApp.iopub_data_rate_limit`.

Current values:
ServerApp.iopub_data_rate_limit=1000000.0 (bytes/sec)
ServerApp.rate_limit_window=3.0 (secs)



## Part 1b: Generate report

In [107]:
## Using subprocess:
import subprocess
subprocess.check_output(["Rscript", "./generate_drone_metadata.R", input])
# from rpy2.robjects.packages import importr


Loading required package: magrittr
uasimg (version 1.8.3)
Bug reports: https://github.com/ucanr-igis/uasimg/issues
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230427_MDG-tulear_UAV-02_1/DCIM
 - Looking for image files (all image files)
 - Found DJI Mavic 2 Pro Hasselblad
 - Running exiftool (this can take a while)...Done.
 - Total file size: 3940 MB
 - Creating footprints...Done.
 - Computing forward overlap...Done.
 - Cache saved
 - Metadata file not found
All done
2023-04-27_12-19-12_323JPEGs
 - computing thumbnail file names...Done.
 - thumbnails already exist
 - Done.


processing file: uas_report_metrics.Rmd
output file: uas_report_metrics.knit.md


Output created: METADATA/Report_2023-04-27_12-19-12_323JPEGs.html
Done.
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230430_MDG-nosyve_UAV-02_1/DCIM
 - Looking for image files (all image files)
 - Found DJI Mavic 2 Pro Hasselblad
 - Running exiftool (this can take a while)...Done.
 - Total file size: 3977 MB
 - Creating footprints...Done.
 - Comp

b'[1] "/home/sylvain/HDD5To/DATA/MADAGASCAR"\n[1] "processing: /home/sylvain/HDD5To/DATA/MADAGASCAR/20230427_MDG-tulear_UAV-02_1"\n[1] "METADATA folder available"\n1/27                   \n2/27 [unnamed-chunk-1] \n3/27                   \n4/27 [unnamed-chunk-2] \n5/27                   \n6/27 [setup]           \n7/27                   \n8/27 [data_uris_insert]\n9/27                   \n10/27 [show_flight_info]\n11/27                   \n12/27 [leaflet_ctr]     \n13/27                   \n14/27 [fp_tab]          \n15/27                   \n16/27 [leaflet_fp]      \n17/27                   \n18/27 [kml_links]       \n19/27                   \n20/27 [nothingtodo]     \n21/27                   \n22/27 [unnamed-chunk-3] \n23/27                   \n24/27 [unnamed-chunk-4] \n25/27                   \n26/27 [unnamed-chunk-5] \n27/27                   \n/usr/bin/pandoc +RTS -K512m -RTS uas_report_metrics.knit.md --to html4 --from markdown+autolink_bare_uris+tex_math_single_backslash --output /m

## Part 2: Generate metadata

In [219]:
# Import packages and modules
import os
import shutil
import pandas as pd
import geopandas as gpd
import datetime
# from IPython.display import display
import argparse
import json
import pycountry
os.chdir(dronemdt_folder)
from meteo_helper import meteo
from read_metadata import *
from exif_helper import *
from enriched_func import *
from zenodo_helper import *
from zip_helper import *
from geoflow_helper import *
from raster_helper import *
from process_webodm import *
from settings import *
import hashlib
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [9]:
### Filter foder name
folder_name = filter_folder_name(input, 'UAV')
folder_name

['20230505_MDG-sarodrano_UAV-02_2',
 '20230504_MDG-atoll_UAV-02_1',
 '20230917_MDG-nosy-fanhy_UAV-02_1',
 '20230430_MDG-nosyve_UAV-02_3',
 '20230502_MDG-sarodrano_UAV-02_1',
 '20230502_MDG-anakao_UAV-02_1',
 '20230427_MDG-tulear_UAV-02_1',
 '20230916_MDG-nosy-sakatia_UAV-02_1',
 '20230917_MDG-nosy-fanhy_UAV-02_2',
 '20230917_MDG-nosy-fanhy_UAV-02_3',
 '20230915_MDG-nosy-sakatia_UAV-02_1',
 '20230507_MDG-massif-des-roses_UAV-02_1',
 '20230507_MDG-ifaty_UAV-02_1',
 '20230912_MDG-nosy-sakatia_UAV-02_1',
 '20230504_MDG-saintaugustin_UAV-02_1',
 '20230915_MDG-nosy-sakatia_UAV-02_2',
 '20230503_MDG-iot_UAV-02_1',
 '20230917_MDG-nosy-fanhy_UAV-02_4',
 '20230430_MDG-nosyve_UAV-02_2',
 '20230505_MDG-sarodrano_UAV-02_1',
 '20230507_MDG-massif-des-roses_UAV-02_2',
 '20230430_MDG-nosyve_UAV-02_1',
 '20230502_MDG-iot_UAV-02_1']

In [39]:
### Put data in basic panda dataframe
df = {}
df = basic_geoflow_df(folder_name)
df.head()

Identifier                                   Title  \
0   20230505_MDG-sarodrano_UAV-02_2   title:20230505 mdg sarodrano uav 02 2   
1       20230504_MDG-atoll_UAV-02_1       title:20230504 mdg atoll uav 02 1   
2  20230917_MDG-nosy-fanhy_UAV-02_1  title:20230917 mdg nosy fanhy uav 02 1   
3      20230430_MDG-nosyve_UAV-02_3      title:20230430 mdg nosyve uav 02 3   
4   20230502_MDG-sarodrano_UAV-02_1   title:20230502 mdg sarodrano uav 02 1   

                                  Description       Subject       Creator  \
0  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
1  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
2  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
3  abstract:'No           \n\ndescription\n!'  project:None  creator:None   
4  abstract:'No           \n\ndescription\n!'  project:None  creator:None   

                                          Date     Type Language  \
0  publication:2023-10-29_\nedition:2023-10-29  dataset      eng   
1  publication:2023-10-29_\nedition:2023-10-29  dataset      eng   
2  publication:2023-10-29_\nedition:2023-10-29  dataset      eng   
3  publication:2023-10-29_\nedition:2023-10-29  dataset      eng   
4  publication:2023-10-29_\nedition:2023-10-29  dataset      eng   

  SpatialCoverage TemporalCoverage Relation  \
0                    MDG-sarodrano     None   
1                    MDG-sarodrano     None   
2                    MDG-sarodrano     None   
3                    MDG-sarodrano     None   
4                    MDG-sarodrano     None   

                                                                                                     Rights  \
0  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
1  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
2  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
3  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   
4  useLimitation:Utilisation libre sous réserve de mentionner la source (a minima le nom du producteur) ...   

  Provenance              Format  Data  
0       None  resource:image/jpg  None  
1       None  resource:image/jpg  None  
2       None  resource:image/jpg  None  
3       None  resource:image/jpg  None  
4       None  resource:image/jpg  None

In [11]:
### Define Metadata file
md_file = 'metadata.txt'
### Parse global metadata
mdt_df_glob = global_mdt(input, md_file)
#### Enrich metadata
enrich_drone_mdt(input, df, md_file, mdt_df_glob)

INFO: Global `metadata.txt` found !
WARN: No metadata.txt in /home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/METADATA to parse
INFO: GPS Folder found
Format id to obtain date, country name, optionnal place, and platform
####################
### 2. Enrich Title
####################
INFO: Using glocal title
Images drone {platform}, {place}, {country} - {date}
format field
####################
### 8. Enrich Language
####################
INFO: Using glocal language
####################
### 4. Enrich Subject
####################
INFO: Using glocal theme
INFO: Using glocal project
####################
### 5. Enrich Creator
####################
INFO: Using glocal author
INFO: Using glocal publisher
INFO: Using glocal owner
INFO: Using glocal pointOfContact
INFO: Using glocal processor
####################
### 11. Enrich Relation
####################
INFO: Using glocal thumbnail
INFO: Using glocal http
####################
### Reading DCIM folder
####################
Extra

/home/sylvain/DroneMDT/enriched_func.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  enriched = df_global.iloc[0][keyword][0]


/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2
Generate image with a set of images
Nb images:  213
preview 8 x  8
####################
### 10. Enrich TemporalCoverage
####################
####################
### 00. Prepare Provenance (13) and Description (3) 
####################
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/DCIM/DJI_0159.JPG
####################
Fetching open-meteo
####################
Location: -23.50887915, 43.7389564
Begin: 2023-05-05 13-10-25 - End: 2023-05-05 13-25-59
Model: best_match


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  1951    0  1951    0     0   7478      0 --:--:-- --:--:-- --:--:--  7503


Convert Dataframe to UTM
Index(['FileName', 'GPSLatitude', 'GPSLongitude', 'GPSAltitude',
       'FlightRollDegree', 'FlightPitchDegree', 'FlightYawDegree',
       'GimbalRollDegree', 'GimbalPitchDegree', 'GimbalYawDegree',
       'ImageWidth', 'ImageLength', 'BitsPerSample', 'ImageDescription',
       'Make', 'Model', 'Orientation', 'SamplesPerPixel', 'XResolution',
       'YResolution', 'ResolutionUnit', 'Software', 'DateTime',
       'YCbCrPositioning', 'ExifOffset', 'GPSVersionID', 'ThumbnailImageWidth',
       'ThumbnailImageLength', 'ThumbnailCompression', 'ThumbnailXResolution',
       'ThumbnailYResolution', 'ThumbnailResolutionUnit',
       'ThumbnailJPEGInterchangeFormat',
       'ThumbnailJPEGInterchangeFormatLength', 'ExposureTime', 'FNumber',
       'ExposureProgram', 'ISOSpeedRatings', 'ExifVersion', 'DateTimeOriginal',
       'DateTimeDigitized', 'ComponentsConfiguration', 'ExposureBiasValue',
       'MaxApertureValue', 'MeteringMode', 'LightSource', 'Flash',
       'Foc

...

Convert Dataframe to UTM
Index(['FileName', 'GPSLatitude', 'GPSLongitude', 'GPSAltitude',
       'FlightRollDegree', 'FlightPitchDegree', 'FlightYawDegree',
       'GimbalRollDegree', 'GimbalPitchDegree', 'GimbalYawDegree',
       'ImageWidth', 'ImageLength', 'BitsPerSample', 'ImageDescription',
       'Make', 'Model', 'Orientation', 'SamplesPerPixel', 'XResolution',
       'YResolution', 'ResolutionUnit', 'Software', 'DateTime',
       'YCbCrPositioning', 'ExifOffset', 'GPSVersionID', 'ThumbnailImageWidth',
       'ThumbnailImageLength', 'ThumbnailCompression', 'ThumbnailXResolution',
       'ThumbnailYResolution', 'ThumbnailResolutionUnit',
       'ThumbnailJPEGInterchangeFormat',
       'ThumbnailJPEGInterchangeFormatLength', 'ExposureTime', 'FNumber',
       'ExposureProgram', 'ISOSpeedRatings', 'ExifVersion', 'DateTimeOriginal',
       'DateTimeDigitized', 'ComponentsConfiguration', 'ExposureBiasValue',
       'MaxApertureValue', 'MeteringMode', 'LightSource', 'Flash',
       'Foc

/home/sylvain/DroneMDT/enriched_func.py:14: FutureWarning: Series.__getitem__ treating keys as positions is deprecated. In a future version, integer keys will always be treated as labels (consistent with DataFrame behavior). To access a value by position, use `ser.iloc[pos]`
  enriched = df_global.iloc[0][keyword][0]


/home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1
Generate image with a set of images
Nb images:  303
preview 8 x  8
####################
### 10. Enrich TemporalCoverage
####################
####################
### 00. Prepare Provenance (13) and Description (3) 
####################
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1/DCIM/DJI_0920.JPG
####################
Fetching open-meteo
####################
Location: -23.493549299999998, 43.75718785
Begin: 2023-05-02 16-10-31 - End: 2023-05-02 16-50-41
Model: best_match


  % Total    % Received % Xferd  Average Speed   Time    Time     Time  Current
                                 Dload  Upload   Total   Spent    Left  Speed
100  2004    0  2004    0     0   7687      0 --:--:-- --:--:-- --:--:--  7707


Convert Dataframe to UTM
Index(['FileName', 'GPSLatitude', 'GPSLongitude', 'GPSAltitude',
       'FlightRollDegree', 'FlightPitchDegree', 'FlightYawDegree',
       'GimbalRollDegree', 'GimbalPitchDegree', 'GimbalYawDegree',
       'ImageWidth', 'ImageLength', 'BitsPerSample', 'ImageDescription',
       'Make', 'Model', 'Orientation', 'SamplesPerPixel', 'XResolution',
       'YResolution', 'ResolutionUnit', 'Software', 'DateTime',
       'YCbCrPositioning', 'ExifOffset', 'GPSVersionID', 'ThumbnailImageWidth',
       'ThumbnailImageLength', 'ThumbnailCompression', 'ThumbnailXResolution',
       'ThumbnailYResolution', 'ThumbnailResolutionUnit',
       'ThumbnailJPEGInterchangeFormat',
       'ThumbnailJPEGInterchangeFormatLength', 'ExposureTime', 'FNumber',
       'ExposureProgram', 'ISOSpeedRatings', 'ExifVersion', 'DateTimeOriginal',
       'DateTimeDigitized', 'ComponentsConfiguration', 'ExposureBiasValue',
       'MaxApertureValue', 'MeteringMode', 'LightSource', 'Flash',
       'Foc

In [111]:
# Set prefix for generated json and csv entities
out_prefix = datetime.datetime.now().strftime('%Y%m%d-%H%M%S')
out_prefix
# out_prefix = '20231027-104053'

'20231101-161132'

In [45]:
# Visualize output
df.head()

Identifier  \
0   20230505_MDG-sarodrano_UAV-02_2   
1       20230504_MDG-atoll_UAV-02_1   
2  20230917_MDG-nosy-fanhy_UAV-02_1   
3      20230430_MDG-nosyve_UAV-02_3   
4   20230502_MDG-sarodrano_UAV-02_1   

                                                              Title  \
0   title:Images drone UAV, Sarodrano, Madagascar - 20230505 - 02_2   
1       title:Images drone UAV, Atoll, Madagascar - 20230504 - 02_1   
2  title:Images drone UAV, Nosy fanhy, Madagascar - 20230917 - 02_1   
3      title:Images drone UAV, Nosyve, Madagascar - 20230430 - 02_3   
4   title:Images drone UAV, Sarodrano, Madagascar - 20230502 - 02_1   

                                                                                                Description  \
0  abstract:"Jeu de données composé d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Sarodr...   
1  abstract:"Jeu de données composé d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Atoll,...   
2  abstract:"Jeu de données composé d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Nosy f...   
3  abstract:"Jeu de données composé d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Nosyve...   
4  abstract:"Jeu de données composé d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Sarodr...   

                                                                                                    Subject  \
0  theme[General]:Madagascar,drone,lagon,lagoon,corail,reef,G2OI,grand observatoire de l'océan Indien,ru...   
1  theme[General]:Madagascar,drone,lagon,lagoon,corail,reef,G2OI,grand observatoire de l'océan Indien,ru...   
2  theme[General]:Madagascar,drone,lagon,lagoon,corail,reef,G2OI,grand observatoire de l'océan Indien,ru...   
3  theme[General]:Madagascar,drone,lagon,lagoon,corail,reef,G2OI,grand observatoire de l'océan Indien,ru...   
4  theme[General]:Madagascar,drone,lagon,lagoon,corail,reef,G2OI,grand observatoire de l'océan Indien,ru...   

                                                                                                    Creator  \
0  author:sylvain.poulain@ird.fr,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain....   
1  author:sylvain.poulain@ird.fr,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain....   
2  author:sylvain.poulain@ird.fr,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain....   
3  author:sylvain.poulain@ird.fr,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain....   
4  author:sylvain.poulain@ird.fr,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain....   

                                          Date     Type Language  \
0  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
1  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
2  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
3  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
4  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2023-05-05 13-10-25 - 2023-05-05 13-25-59   
1              NaN  2023-05-04 10-29-18 - 2023-05-04 11-04-15   
2              NaN  2023-09-17 08-42-17 - 2023-09-17 08-55-11   
3              NaN  2023-04-30 13-21-54 - 2023-04-30 13-39-27   
4              NaN  2023-05-02 17-46-21 - 2023-05-02 17-54-30   

                                                                                                   Relation  \
0  thumbnail:G2OI@https://g2oi.ird.fr/static/img/logo_ird.png_\nhttp:Website G2OI[G2OI Website]@https://...   
1  thumbnail:G2OI@https://g2oi.ird.fr/static/img/logo_ird.png_\nhttp:Website G2OI[G2OI Website]@https://...   
2  thumbnail:G2OI@https://g2oi.ird.fr/static/img/logo_ird.png_\nhttp:Website G2OI[G2OI Website]@https://...   
3  thumbnail:G2OI@https://g2oi.ird.fr/static/img/logo_ird.png_\nhttp:Website G2OI[G2OI Website]@https://...   
4  thum

In [47]:
# Visualize Description
print(df.iloc[0]['Description'])
print(df.iloc[0]['Data'])

abstract:"Jeu de données composé d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Sarodrano, Madagascar à la date suivante : 20230505.
<br />Les vols ont été réalisés en partenariat avec l'IH.SM dans le but de créer des modèles numériques d'élévations pour cartographier l'écosystème marin.
<br />
<br /><b>Le dépôt est composé des éléments suivants:</b>
<br />    - 00_: Planche d'aperçu des images
<br />    - DCIM.zip: Images brutes issues du drone
<br />    - GPS.zip: Geopackage contenant l’emprise du survol ainsi que la géolocalisation des images accompagnées de leurs miniatures dans la table d’attribut en base64
<br />    - METADATA.zip: Métadonnées au format ISO19115, Rapports avec miniatures des images de drone (dossier tb) et statistiques de vols.
<br />
<br /><b>Arborescence d'origine:</b>
<br />│  └─ 20230505_MDG-sarodrano_UAV-02_2
<br />│--------  └─ DCIM
<br />│--------  └─ GPS
<br />│--------  └─ METADATA
<br />│----------------  └─ tb
<br />
<br /><b>Information

In [15]:
##############
#### ISO 19115 config
##############
## Export to csv
df.to_csv(os.path.join(output, out_prefix + "_iso19115-metadata.csv"), quoting=1, quotechar='"', index=False)
## Generate json
iso19115config = {'profile': {'id': 'iso19115', 
                              'name': 'iso19115', 
                              'project': 'Generate iso19115 with Geoflow', 
                              'organization': 'IRD', 
                              'environment': {'file': '.env', 
                                              'hide_env_vars': ['MOTDEPASSE']}, 
                              'logos': ['https://en.ird.fr/sites/ird_fr/files/2019-08/logo_IRD_2016_BLOC_UK_COUL.png'], 
                              'mode': 'entity'}, 
                  'metadata': {'entities': 
                               [{'handler': 'csv', 
                                 'source': os.path.join(output, out_prefix) + "_iso19115-metadata.csv"}], 
                               'contacts': 
                               [{'handler': 'csv', 
                                 'source': 'https://drive.ird.fr/s/EYS3qccyB28PrA9/download/geoflow_g2oi_contacts.csv'}]}, 
                  'software': [], 
                  'actions': 
                  [{'id': 'geometa-create-iso-19115',
                    'options' : 
                    {"logo": True}, 
                    "run": True}]}

# Export json to file
with open(os.path.join(output, out_prefix + '_iso19115-config.json'), 'w') as f:
    json.dump(iso19115config, f, indent=4)

In [128]:
# Optional : could start from here => reload dataframe from csv
df = {}
df = pd.read_csv(os.path.join(output, out_prefix + "_iso19115-metadata.csv"))

In [16]:
### Execute geoflow
xml19115 = run_geoflow(os.path.join(output, out_prefix + '_iso19115-config.json'), geoflow_folder)
os.chdir(dronemdt_folder)

R[write to console]: Rows: 129 Columns: 14

R[write to console]: ── Column specification ────────────────────────────────────────────────────────
Delimiter: ","
chr (14): Identifier, Email, OrganizationName, PositionName, LastName, First...

R[write to console]: 
ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.

R[write to console]: Rows: 23 Columns: 15

R[write to console]: ── Column specification ────────────────────────────────────────────────────────
Delimiter: ","
chr (15): Identifier, Title, Description, Subject, Creator, Date, Type, Lang...

R[write to console]: 
ℹ Use `spec()` to retrieve the full column specification for this data.
ℹ Specify the column types or set `show_col_types = FALSE` to quiet this message.

R[write to console]: Loading required package: geometa

R[write to console]: Loading required package: ows4R



In [17]:
# Geoflow job log folder
print(xml19115[0])

/home/sylvain/geoflow-g2oi/jobs/20231027104203


In [ ]:
## Copy generated ISO19115 to original metadata folder
for id in range(len(df)):
    jobs19115 = xml19115[0] + '/entities/' + df.iloc[id]['Identifier'] + '/metadata/'
    fname19115 = df.iloc[id]['Identifier'] + '_ISO-19115.xml'
    if fname19115 in os.listdir(jobs19115):
        shutil.copyfile(jobs19115+fname19115, 
                        input + "/" + df.iloc[id]['Identifier'] + '/METADATA/' + fname19115)

## Part 3. Prepare RAW data to Zenodo

### ZIP all folders and reference files in dataframe (data column)

In [ ]:
### Zip all folders
zip_each_folder(input, df)

In [129]:
### Reference Zip's in Dataframe
for zip in range(len(df)):
    source = []
    sess_path = os.path.join(input, df.iloc[zip]['Identifier'])
    source = os.listdir(sess_path)
    # print(len(source))
    # print(source)
    if len(source) < 1:
        pass
    else:
        source_file = []
        for file in range(len(source)):
            if "PROCESSED_DATA" in source[file]:
                pass
            elif "000_photogrammetry_report.pdf" in source[file]:
                pass                
            else:
                if os.path.isfile(os.path.join(sess_path, source[file])):
                    if len(source) < 2:
                        df.iloc[zip, df.columns.get_loc('Data')] = "source:" + source[file] + "@" + sess_path + "/" + source[file] + "_\n" + "sourceType:other_\nsourceZip:false"
                        source_file = source[file]
                    else:
                        source_file.append(source[file])
                        # df.iloc[zip, df.columns.get_loc('Data')] = "source:" + source[file] + "@" + sess_path + source[file] + "_\n" + "sourceType:other_\nsourceZip:false"
        if ".zip" in  df.iloc[zip, df.columns.get_loc('Data')]:
            print("zip already in Data")
            pass
        else:
            df.iloc[zip, df.columns.get_loc('Data')] = "source:"
            for i in range(len(source_file)):
                print(source_file[i], i, "/", len(source_file))
                df.iloc[zip, df.columns.get_loc('Data')] =  str(df.iloc[zip, df.columns.get_loc('Data')]) + source_file[i] + "@" + sess_path + "/" + source_file[i] + ","
    
    if "," in str(df.iloc[zip, df.columns.get_loc('Data')])[-1]:
        df.iloc[zip, df.columns.get_loc('Data')] = str(df.iloc[zip, df.columns.get_loc('Data')])[:-1] + "_\n" + "sourceType:other_\nupload:true"

df.iloc[zip]['Data']


GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 5
00_sample_rawdata_overview.png 1 / 5
DCIM.zip 2 / 5
METADATA.zip 3 / 5
VIDEO.zip 4 / 5
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 4
DCIM.zip 2 / 4
METADATA.zip 3 / 4
GPS.zip 0 / 4
00_sample_rawdata_overview.png 1 / 

'source:GPS.zip@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1/GPS.zip,00_sample_rawdata_overview.png@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1/00_sample_rawdata_overview.png,DCIM.zip@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1/DCIM.zip,METADATA.zip@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1/METADATA.zip_\nsourceType:other_\nupload:true'

### Generate config files for geoflow or re-use dataframe later

In [130]:
### Export raw data df to csv
fname = out_prefix + '_zenodo-rawdata'
df.to_csv(os.path.join(output, fname + ".csv"), quoting=1, quotechar='"', index=False)

### Configure and export Zenodo json
# SANDBOX
# zen_json = zenodo_json(fname, 'sandbox', output, out_prefix)
# PRODUCTION
zen_json = zenodo_json(fname, 'no_sandbox', output, out_prefix)
with open(os.path.join(output, out_prefix + '_rawfiles-config.json'), 'w') as f:
    json.dump(zen_json, f, indent=4)


In [147]:
# Optional : could start from here => reload dataframe from csv
df = {}
df = pd.read_csv(os.path.join(output, out_prefix + "_zenodo-rawdata.csv"))
# df.head()
print(df.iloc[0]["Identifier"])
print(df.iloc[0]["Subject"])
print(df.iloc[0]["Data"])

id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10064364
theme[General]:Madagascar,drone,lagon,lagoon,corail,reef,G2OI,grand observatoire de l'océan Indien,rugosité,récif,struture récifale,coraux,drone,uav,uas,DEM,digital elevation model,orthophotographie,orthophotography,photogrammétrie,photogrammetry,SfM,Structure from Motion,OpenDroneMap,opendata,dji,mavic_
project:G2OI@https://www.ird.fr/projet-g2oi-grand-observatoire-de-locean-indien
source:GPS.zip@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/GPS.zip,00_sample_rawdata_overview.png@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/00_sample_rawdata_overview.png,DCIM.zip@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/DCIM.zip,METADATA.zip@/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/METADATA.zip_
sourceType:other_
upload:true


## Part 4. Upload RAW data to Zenodo

### Execute Geoflow to upload to Zenodo
/!\ DISABLED SINCE FRIDAY 2023 10 13 /!\
/!\ Zenodo upgrade /!\

In [26]:
# ### Execute geoflow :: upload to geoflow
# # upload_raw_to_zenodo = 
# config_raw = os.path.join(output, out_prefix + '_rawfiles-config.json')
# # run_geoflow(config_raw, geoflow_folder)
# os.chdir(geoflow_folder)
# # subprocess.run(["R", "-e", "geoflow::initWorkflow('{}')".format(config_raw)], capture_output=False)
# subprocess.call(["R", "-e", "geoflow::executeWorkflow('{}')".format(config_raw)],
#                 stdout=subprocess.DEVNULL, stderr=subprocess.STDOUT,)
# os.chdir(dronemdt_folder)

### Upload to Zenodo with Python

In [132]:
%load_ext autoreload
%autoreload 2

# del(zenul)
from zenodo_helper import *
# help(zenul)
# data_zip

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [149]:
### Upload to Zenodo
print("#### Upload zip files to Zenodo")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    # print("Dataset:", zipul, "/" ,len(df))
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url

    #### Extract source from Data in dataframe
    data_zip = df.iloc[zipul]['Data'].split('source:')[1].split('_\n')[0]
    if "," in data_zip:
        data_ziptemp = data_zip.split(',')
        data_zip = []
        for dt in range(len(data_ziptemp)):
            data_zip.append(data_ziptemp[dt].split('@')[0])
    else:
        data_zip = data_zip.split('@')[0]
    # data_zip = source_file
    print(data_zip)

    ### Put Metadata or verify if doi exists (Metadata not updated if doi exists)
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('\n')[0].split('.')[-1]
        print("DOI already present: ",doi_raw)
        getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        zenval = zenvar(getrecid)
    else:
        print("Initialize deposit")
        r = check_token(zenodo_baseurl, ACCESS_TOKEN)
        zenval = zenvar(r)
        print("prereserved doi:"+zenval[1])
        print("Write DOI to dataframe")
        dfzen = df
        if 'id:' in dfzen.iloc[zipul]['Identifier']:
            pass
        else:
            dfzen.iloc[zipul, dfzen.columns.get_loc('Identifier')] = "id:" + dfzen.iloc[zipul]['Identifier'] + "_\ndoi:" + zenval[1]
            dfzen.iloc[zipul, dfzen.columns.get_loc("Provenance")] = dfzen.iloc[zipul]["Provenance"] + "_\nprocess:Raw dataset uploaded to " + base_url.split('api')[0] + "record/" + str(zenval[2])
            
        print("Enrich upload with metadata")
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
        if zen_metadata.status_code > 400:
            print("error in metadata, please check there is no double keywords: \n" + zen_metadata.text)
            break
        
    # print(zen_metadata.text)       
    print("upload data")
    print("Trying upload number: 1")

    for file in data_zip:
        ul_count = 1
        ### Control Filename
        # while file not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
        ### Control md5 checksum:
        ful = os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file)
        print(ful)
        with open(ful, "rb") as file_to_check:
            # Open,close, read file and calculate MD5 on its contents 
            # read contents of the file
            ## Python 3.10
            fh = file_to_check.read() 
            # pipe contents of the file through
            digest = hashlib.md5(fh)
            ## End Python 3.10
            # digest = hashlib.file_digest(file_to_check, "md5") ### Python 3.11 only
        print("    md5:", digest.hexdigest())
        while digest.hexdigest() not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
            #Reset connection every 15 tries
            if ul_count == 15:
                getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
                zenval = zenvar(getrecid)
            
            file_on_server = zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
            ### Clean wrong checksum
            if file in file_on_server.text:
                print("    clean wrong files")
                for fs in range(len(file_on_server.json())):
                    if file == file_on_server.json()[fs]['filename']:
                        # print("    sleep 5: computing checksum on server")
                        # time.sleep(15)
                        print("    checksum on server", file_on_server.json()[fs]['checksum'])
                        furl = file_on_server.json()[fs]["links"]["self"]
                        file_to_remove = zen_del_file(furl, ACCESS_TOKEN)
                        
            file_list = [file]            
            zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
            print("        ", zen_upload.text)
            if zen_upload.status_code == 404:
                print("Version doesn't exists ! Please check your record_id")
                break
            else:
                ul_count += 1
                print("    Retry number: " + str(ul_count))
                if zen_upload.status_code == 403:
                    print("        Friday 13th 2023 nightmare => permission denied!")
                    time.sleep(5)      
            
    # zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), data_zip)
    # # for file in data_zip:
    # #     print("Uploading: ", file)
    # #     print("curl", "--upload-file", os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file), zenval[0] + "/" + file + "?" + "k3LQP8uj4HtpRbjMMXMIUBeRJr0UFELUwjyXWIakTHh0xP9p5PhZ7bzCqRN1")
    # #     subprocess.check_output(["curl", "--upload-file", 
    # #                              os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file),
    # #                              zenval[0] + "/" + file + "?" + "k3LQP8uj4HtpRbjMMXMIUBeRJr0UFELUwjyXWIakTHh0xP9p5PhZ7bzCqRN1"
    # #                                           ])
    # if zen_upload.status_code != 201:
    #     for file in data_zip:
    #         file_list = [file]
    #         zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
    #         # zen_upload = zenul(zenvar(newv), ACCESS_TOKEN, os.getcwd(), test_list)
    #         # zen_upload = zenul2(zenodo_baseurl, str(zenval[-1]), ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), data_zip)
    #         print("Upload status OK? " + str(zen_upload.ok))
    #         print("Control files: first pass")
    #         ul_count = 1
    #         while zen_upload.status_code != 201:
    #             if zen_upload.status_code == 404:
    #                 print("Version doesn't exists ! Please check your record_id")
    #                 break
    #             else:
    #                 ul_count += 1
    #                 print("Retry number: " + str(ul_count))
    #                 zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
    #                 if zen_upload.status_code == 403:
    #                     print("        Friday 13th 2023 nightmare => permission denied!")
    #                     time.sleep(5)
                    
            # zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
            ## Too agressive                
            # print("Control files: second pass")
            # if zen_upload.status_code == 201:
            #     # files_ul = zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
            #     # while len(zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).json()) != len(data_zip):
            #     while file not in zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).json():
            #         if zen_upload.status_code == 404:
            #             print("Version doesn't exists ! Please check your record_id")
            #             break
            #         else:
            #             ul_count += 1
            #             print("Retry number: " + str(ul_count))
            #             zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
            #             # files_ul = zenfiles(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))       
            

    ### Publish to Zenodo
    print("Publish record")
    zenpublish(zenodo_baseurl, ACCESS_TOKEN, zenval[2])

#### Upload zip files to Zenodo

Dataset: 1 / 23 
     id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10064364
['GPS.zip', '00_sample_rawdata_overview.png', 'DCIM.zip', 'METADATA.zip']
DOI already present:  10064364
upload data
Trying upload number: 1
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/GPS.zip
    md5: d414105bab4b5b0537f6788ce34e2c30
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/00_sample_rawdata_overview.png
    md5: fb8c4f1f8a55f7a842702b6f336dbf66
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/DCIM.zip
    md5: 180467303035a8af4ee239f329603e4b
/home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2/METADATA.zip
    md5: aed8a0130430823d47bcfe2b88bb4891
Publish record

Dataset: 2 / 23 
     id:20230504_MDG-atoll_UAV-02_1_
doi:10.5281/zenodo.10064368
['GPS.zip', '00_sample_rawdata_overview.png', 'DCIM.zip', 'METADATA.zip']
DOI already present:  10064368
upload data
Trying upload number

In [150]:
### Check DOI's

for doi in range(len(df)):
    print(df.iloc[doi]["Identifier"])

id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10064364
id:20230504_MDG-atoll_UAV-02_1_
doi:10.5281/zenodo.10064368
id:20230917_MDG-nosy-fanhy_UAV-02_1_
doi:10.5281/zenodo.10064384
id:20230430_MDG-nosyve_UAV-02_3_
doi:10.5281/zenodo.10064392
id:20230502_MDG-sarodrano_UAV-02_1_
doi:10.5281/zenodo.10064397
id:20230502_MDG-anakao_UAV-02_1_
doi:10.5281/zenodo.10064401
id:20230427_MDG-tulear_UAV-02_1_
doi:10.5281/zenodo.10064403
id:20230916_MDG-nosy-sakatia_UAV-02_1_
doi:10.5281/zenodo.10064410
id:20230917_MDG-nosy-fanhy_UAV-02_2_
doi:10.5281/zenodo.10064418
id:20230917_MDG-nosy-fanhy_UAV-02_3_
doi:10.5281/zenodo.10064425
id:20230915_MDG-nosy-sakatia_UAV-02_1_
doi:10.5281/zenodo.10064437
id:20230507_MDG-massif-des-roses_UAV-02_1_
doi:10.5281/zenodo.10064443
id:20230507_MDG-ifaty_UAV-02_1_
doi:10.5281/zenodo.10064452
id:20230912_MDG-nosy-sakatia_UAV-02_1_
doi:10.5281/zenodo.10064456
id:20230504_MDG-saintaugustin_UAV-02_1_
doi:10.5281/zenodo.10064460
id:20230915_MDG-nosy-sakatia_UAV-0

In [137]:
### Export Dataframe to csv
# ### Export Dataframe to csv
csv_published = out_prefix + "_zenodo-rawdata"
df.to_csv(os.path.join(output, csv_published + ".csv"), quoting=1, quotechar='"', index=False)
# ### Export geoflow config to json
if sandbox == True:
    zenodo_url = "https://sandbox.zenodo.org/api"
else:
    zenodo_url = "https://zenodo.org/api"
rawdata_config = {'profile': {'id': 'rawdata', 'name': 'rawdata', 'project': 'Publish rawdata with Geoflow', 'organization': 'IRD', 'environment': {'file': '.env', 'hide_env_vars': ['MOTDEPASSE']}, 'logos': ['https://en.ird.fr/sites/ird_fr/files/2019-08/logo_IRD_2016_BLOC_UK_COUL.png'], 'mode': 'entity'}, 'metadata': {'entities': [{'handler': 'csv', 'source': os.path.join(output, out_prefix) + "_zenodo-rawdata.csv"}], 'contacts': [{'handler': 'csv', 'source': 'https://drive.ird.fr/s/EYS3qccyB28PrA9/download/geoflow_g2oi_contacts.csv'}]}, 'software': [{"id": "my-zenodo","type": "output","software_type": "zenodo","parameters": {"url": zenodo_url,"token": "{{ ZENODO_TOKEN }}","logger": "DEBUG"},"properties": {"clean": {"run": False}}}], 'actions': [{"id": "zen4R-deposit-record","options": {"update_files": True,"communities": "uav","depositWithFiles": True,"publish": False,"update_metadata": True,"strategy": "newversion","deleteOldFiles": True},"run": True}]}
with open(os.path.join(output, out_prefix + '_zenodo-rawdata-config.json'), 'w') as f:
    json.dump(rawdata_config, f, indent=4)

## Part 5. Download from ODM

In [153]:
# Take csv generated from python's zenodo upload as updated dataframe
df = {}
df = pd.read_csv(os.path.join(input, out_prefix + '_zenodo-rawdata.csv'))
df.head()

Identifier  \
0  id:20230505_MDG-sarodrano_UAV-02_2_\ndoi:10.52...   
1  id:20230504_MDG-atoll_UAV-02_1_\ndoi:10.5281/z...   
2  id:20230917_MDG-nosy-fanhy_UAV-02_1_\ndoi:10.5...   
3  id:20230430_MDG-nosyve_UAV-02_3_\ndoi:10.5281/...   
4  id:20230502_MDG-sarodrano_UAV-02_1_\ndoi:10.52...   

                                               Title  \
0  title:Images drone UAV, Sarodrano, Madagascar ...   
1  title:Images drone UAV, Atoll, Madagascar - 20...   
2  title:Images drone UAV, Nosy fanhy, Madagascar...   
3  title:Images drone UAV, Nosyve, Madagascar - 2...   
4  title:Images drone UAV, Sarodrano, Madagascar ...   

                                         Description  \
0  abstract:"Jeu de données composé d’images de d...   
1  abstract:"Jeu de données composé d’images de d...   
2  abstract:"Jeu de données composé d’images de d...   
3  abstract:"Jeu de données composé d’images de d...   
4  abstract:"Jeu de données composé d’images de d...   

                                             Subject  \
0  theme[General]:Madagascar,drone,lagon,lagoon,c...   
1  theme[General]:Madagascar,drone,lagon,lagoon,c...   
2  theme[General]:Madagascar,drone,lagon,lagoon,c...   
3  theme[General]:Madagascar,drone,lagon,lagoon,c...   
4  theme[General]:Madagascar,drone,lagon,lagoon,c...   

                                             Creator  \
0  author:sylvain.poulain@ird.fr,julien.barde@ird...   
1  author:sylvain.poulain@ird.fr,julien.barde@ird...   
2  author:sylvain.poulain@ird.fr,julien.barde@ird...   
3  author:sylvain.poulain@ird.fr,julien.barde@ird...   
4  author:sylvain.poulain@ird.fr,julien.barde@ird...   

                                          Date     Type Language  \
0  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
1  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
2  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
3  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
4  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2023-05-05 13-10-25 - 2023-05-05 13-25-59   
1              NaN  2023-05-04 10-29-18 - 2023-05-04 11-04-15   
2              NaN  2023-09-17 08-42-17 - 2023-09-17 08-55-11   
3              NaN  2023-04-30 13-21-54 - 2023-04-30 13-39-27   
4              NaN  2023-05-02 17-46-21 - 2023-05-02 17-54-30   

                                            Relation  \
0  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
1  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
2  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
3  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
4  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   

                                              Rights  \
0  useLimitation:Utilisation libre sous réserve d...   
1  useLimitation:Utilisation libre sous réserve d...   
2  useLimitation:Utilisation libre sous réserve d...   
3  useLimitation:Utilisation libre sous réserve d...   
4  useLimitation:Utilisation libre sous réserve d...   

                                          Provenance  \
0  statement:"- Camera model and parameters:\n Ma...   
1  statement:"- Camera model and parameters:\n Ma...   
2  statement:"- Camera model and parameters:\n Ma...   
3  statement:"- Camera model and parameters:\n Ma...   
4  statement:"- Camera model and parameters:\n Ma...   

                                              Format  \
0  resource:image/jpg_\ndistribution:application/...   
1  resource:image/jpg_\ndistribution:application/...   
2  resource:image/jpg_\ndistribution:application/...   
3  resource:image/jpg_\ndistribution:application/...   
4  resource:image/jpg_\ndistribution:application/...   

                                                Data  
0  source:GPS.zip@/home/sylvain/HDD5To/DATA/MADAG...  
1  source:GPS.zip@/home/sylvain/HDD5To/DATA/MADAG...  
2  source:GPS.zip@/home/sylvain/HDD5To/DATA/

In [95]:
### Rename project in WebODM
renamed_df = pd.read_csv(os.path.join(input, 'renommage_mdg.csv'), sep=" ")
# print(renamed_df)
odm_projects = list_all_projects()
for projects in range(len(odm_projects)):
    for p in range(len(renamed_df)):
        if renamed_df.iloc[p]["orig"] in odm_projects[projects]['name']:
            print("########\n", projects, odm_projects[projects]['id'], odm_projects[projects]['name'], '\n#########')
            project_id = odm_projects[projects]['id']
            res = requests.post(settings.SERVER + '/api/token-auth/', 
                            data={'username': settings.USERNAME,
                                'password': settings.PASSWORD}).json()
            if 'token' in res:
                print("Still logged-in!")
                token = res['token']
                # PATCH /api/projects/{id}/
                res = requests.patch(settings.SERVER + "/api/projects/{}/".format(odm_projects[projects]['id']), 
                                    headers={'Authorization': 'JWT {}'.format(token)},
                                    data={
                                        'name': renamed_df.iloc[p]["rename"]
                                    }
                                    ).json()
                print("Renamed from: ", odm_projects[projects]['id'], odm_projects[projects]['name'], "\n", renamed_df.iloc[p]["orig"] , "to: ", renamed_df.iloc[p]["rename"])

Successfully Logged-in!
########
id name permissions
----------
160 PyWebODM - 20221024_SYC-aldabra-passe-arm01_UAV-02_28
159 PyWebODM - 20221021_SYC-aldabra-arm01_UAV-02_10
156 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_31
155 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_30
154 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_29
153 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_21
152 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_20
151 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_19
150 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_18
149 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_17
148 PyWebODM - 20221022_SYC-aldabra-passe-dubois_UAV-02_14
147 PyWebODM - 20221022_SYC-aldabra-passe-dubois_UAV-02_13
146 PyWebODM - 20221022_SYC-aldabra-passe-dubois_UAV-02_12
144 PyWebODM - 20221022_SYC-aldabra-arm06_UAV-02_16
143 PyWebODM - 20221022_SYC-aldabra-arm06_UAV-02_15
142 PyWebODM - 20221021_SYC-aldabra-arm01_UAV-02_9
141 PyWebODM - 20221021_SYC-aldabra-arm01_UAV-02_7
139 PyWebODM - 20221025_SYC-al

In [96]:
### SEARCH AND DOWNLOAD FROM ODM
odm_projects = list_all_projects()
for projects in range(len(odm_projects)):
    for p in range(len(df)):
        if df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1] in odm_projects[projects]['name']:
            print(projects, odm_projects[projects]['id'], odm_projects[projects]['name'], odm_projects[projects]['tasks'])
            project_id = odm_projects[projects]['id']
            tasks =  odm_projects[projects]['tasks']
            res = requests.post(settings.SERVER + '/api/token-auth/', 
                            data={'username': settings.USERNAME,
                                'password': settings.PASSWORD}).json()
            if 'token' in res:
                print("Still logged-in!")
                token = res['token']
                for task in range(len(tasks)):
                    task_id = tasks[task]
                    print(task_id)
                    res = requests.get(settings.SERVER + "/api/projects/{}/tasks/{}/download/all.zip".format(project_id, task_id), 
                                    headers={'Authorization': 'JWT {}'.format(token)},
                                    stream=True)
                    # token = res['token']
                    sess_path = os.path.join(input, df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1])
                    file_newname = 'PROCESSED_DATA.zip'
                    ### Reading PROCESSED_DATA folder
                    ### Check and create PROCESSED_DATA Directory if it not exists
                    # process_dir=os.path.join(sess_path, 'PROCESSED_DATA')
                    # if os.path.exists(process_dir):
                    if os.path.exists(sess_path):
                        if 'PROCESSED_DATA.zip' in os.listdir(sess_path):
                            print("INFO: data already found in {} !".format(df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1]))
                        else:
                        #     print("INFO: Create PROCESSED_DATA folder in {} folder")
                        #     os.mkdir(process_dir)
                            print("Downloading all.zip")
                            with open(os.path.join(input, df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1], "all.zip"), 'wb') as f:
                                for chunk in res.iter_content(chunk_size=1024): 
                                    if chunk:
                                        f.write(chunk)
                            # file_newname = "ortho_" + df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1] + ".tif"
                            # file_newname = 'PROCESSED_DATA.zip'
                            print("Renaming all.zip to PROCESSED_DATA.zip")
                            os.rename(os.path.join(sess_path, "all.zip"), os.path.join(sess_path, file_newname))
                            print("Saved " + file_newname)

                        res = requests.get(settings.SERVER + "/api/projects/{}/tasks/{}/download/report.pdf".format(project_id, task_id), 
                                            headers={'Authorization': 'JWT {}'.format(token)},
                                            stream=True)
                        pdf_newname = '000_photogrammetry_report.pdf'
                        if pdf_newname in os.listdir(sess_path):
                            print("INFO: PDF already found in {} !".format(df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1]))
                        else:
                            print("Downloading report.pdf")
                            with open(os.path.join(input, df.iloc[p]['Identifier'].split('_\n')[0].split(':')[1], "report.pdf"), 'wb') as pdf:
                                for chunk in res.iter_content(chunk_size=1024): 
                                    if chunk:
                                        pdf.write(chunk)
                            
                            os.rename(os.path.join(sess_path, "report.pdf"), os.path.join(sess_path, pdf_newname))
                            print("Saved " + pdf_newname)                    
            ### Enrich Metadata
            dfdlodm = df
            dfdlodm.iloc[p, dfdlodm.columns.get_loc('Provenance')] = dfdlodm.iloc[p]["Provenance"] + "_\nprocess:Download from WebODM"
            dfdlodm.iloc[p, dfdlodm.columns.get_loc('Format')] = "resource:image/tiff_\ndistribution:image/tiff[GeoTIFF]"
            dfdlodm.iloc[p, dfdlodm.columns.get_loc('Data')] = pdf_newname + "@"+ os.path.join(sess_path, pdf_newname) + "," + file_newname + "@"+ os.path.join(sess_path, file_newname) + "_\nsourceType:other_\nsourceZip:False"

Successfully Logged-in!
########
id name permissions
----------
199 ALD_FRAMES_SUBSET_-9.3734_46.2131_2transectsFilt_RAW
198 ALD_FRAMES_SUBSET_-9.3734_46.2131_2transectsFilt
197 ALD_FRAMES_SUBSET_-9.3734_46.2131_rad_30_1698667597s
196 PyWebODM - 20230430_MDG-Nosy-Ve_UAV-01_3
195 PyWebODM - 20230502_MDG-Sarodrano-IOT_UAV-01_5
194 PyWebODM - 20230427_MDG-Toliara-Mangroves_UAV-01_1
193 20230430_MDG-Nosy-Ve_UAV-01_6
189 PyWebODM - 20230916_MDG-nosy-sakatia_UAV-02_1
188 20230906_REU-BOUCAN_ASV-1_01_frames_shortset_01_GEOTXT
187 ALD_DUBOIS_SUBSET_-9.4106_46.2109_rad_15_1698318058
165 20230906_REU-BOUCAN_ASV-1_01_frames_shortset_01
160 PyWebODM - 20221024_SYC-aldabra-passe-arm01_UAV-02_28
159 PyWebODM - 20221021_SYC-aldabra-arm01_UAV-02_10
156 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_31
155 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_30
154 PyWebODM - 20221024_SYC-aldabra-gigi_UAV-02_29
153 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_21
152 PyWebODM - 20221023_SYC-aldabra-arm06_UAV-02_20


In [154]:
### Reformat dataframe

for entities in range(len(df)):
    sess_path = os.path.join(
        input, df.iloc[entities]["Identifier"].split("_\n")[0].split(":")[1]
    )
    df.iloc[entities, df.columns.get_loc("Title")] = df.iloc[entities][
        "Title"
    ].replace(
        "Images drone UAV,",
        "Orthophoto & DEM (MNE) issues d'images drone, UAV,",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "Jeu de données composé d’images",
        "Ce jeu de données présente les résultats des traitements photogrammétriques d’images",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "Les vols ont été réalisés dans le but",
        "Les traitements ont été réalisés avec le logiciel OpenDroneMap à partir des images brutes fournies dans la première version de ce DOI.\n<br />Les vols ont été réalisés dans le but",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "<br /><b>Le dépôt est composé",
        "<br /><br />Le paramétrage du logiciel OpenDroneMap est partagé pour permettre la reproductibilité ou l'amélioration des traitements proposés:<br />\n[\n<br />        {\n<br />            'name': 'orthophoto-resolution',\n<br />            'value': 1\n<br />        },\n<br />        {\n<br />            'name': 'auto-boundary',\n<br />            'value': true\n<br />        },\n<br />        {\n<br />            'name': 'dem-resolution',\n<br />            'value': '2.0'\n<br />        },\n<br />        {\n<br />            'name': 'dsm',\n<br />            'value': true\n<br />        }\n<br />    ]\n<br />\n<br /><b>Le dépôt est composé",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "<br />    - METADATA.zip: Métadonnées au format ISO19115, Rapports avec miniatures des images de drone (dossier tb) et statistiques de vols.",
        "<br />    - METADATA.zip: Métadonnées au format ISO19115, Rapports avec miniatures des images de drone (dossier tb) et statistiques de vols.\n<br />    - PROCESSED_DATA.zip: Orthophoto, DEM, nuages de points, ...",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "<br />│----------------  └─ tb",
        "<br />│----------------  └─ tb\n<br />│--------  └─ PROCESSED_DATA",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "\n<br />Les dépôts suivants comprennent les données traitées avec OpenDroneMap",
        "",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace(
        "\n<br />D'autres versions plus récentes de ce dépôt sont disponibles. Ces dernières comprennent notamment les données traitées avec OpenDroneMap",
        "",
    )
    df.iloc[entities, df.columns.get_loc("Description")] = df.iloc[entities][
        "Description"
    ].replace("RAW DATA", "PROCESSED DATA")
    df.iloc[entities, df.columns.get_loc("Provenance")] = (
        df.iloc[entities]["Provenance"] + "_\nprocess:Download from WebODM"
    )
    df.iloc[
        entities, df.columns.get_loc("Format")
    ] = "resource:image/tiff_\ndistribution:image/tiff[GeoTIFF]"
    df.iloc[entities, df.columns.get_loc("Data")] = (
        "source:"
        + pdf_newname
        + "@"
        + os.path.join(sess_path, pdf_newname)
        + ","
        + file_newname
        + "@"
        + os.path.join(sess_path, file_newname)
        + "_\nsourceType:other"
    )


In [156]:
print(df.iloc[0]["Identifier"])
print(df.iloc[0]["Title"])
print(df.iloc[0]["Description"])
print(df.iloc[0]["Data"])

id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10064364
title:Orthophoto & DEM (MNE) issues d'images drone, UAV, Sarodrano, Madagascar - 20230505 - 02_2
abstract:"Ce jeu de données présente les résultats des traitements photogrammétriques d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Sarodrano, Madagascar à la date suivante : 20230505.
<br />Les vols ont été réalisés en partenariat avec l'IH.SM dans le but de créer des modèles numériques d'élévations pour cartographier l'écosystème marin.
<br />
<br /><br />Le paramétrage du logiciel OpenDroneMap est partagé pour permettre la reproductibilité ou l'amélioration des traitements proposés:<br />
[
<br />        {
<br />            'name': 'orthophoto-resolution',
<br />            'value': 1
<br />        },
<br />        {
<br />            'name': 'auto-boundary',
<br />            'value': true
<br />        },
<br />        {
<br />            'name': 'dem-resolution',
<br />            'value': '2.0'
<br />    

In [157]:
### Export processed data df to csv
# fname = out_prefix + '_zenodo-rawdata'
# df.to_csv(os.path.join(output, fname + ".csv"), quoting=1, quotechar='"', index=False)
df.to_csv(os.path.join(output, out_prefix + "_processed_data.csv"), quoting=1, quotechar='"', index=False)

In [158]:
# Reload df from WebODM download as updated dataframe
df = {}
df = pd.read_csv(os.path.join(input, out_prefix + '_processed_data.csv'))
df.head()

Identifier  \
0  id:20230505_MDG-sarodrano_UAV-02_2_\ndoi:10.52...   
1  id:20230504_MDG-atoll_UAV-02_1_\ndoi:10.5281/z...   
2  id:20230917_MDG-nosy-fanhy_UAV-02_1_\ndoi:10.5...   
3  id:20230430_MDG-nosyve_UAV-02_3_\ndoi:10.5281/...   
4  id:20230502_MDG-sarodrano_UAV-02_1_\ndoi:10.52...   

                                               Title  \
0  title:Orthophoto & DEM (MNE) issues d'images d...   
1  title:Orthophoto & DEM (MNE) issues d'images d...   
2  title:Orthophoto & DEM (MNE) issues d'images d...   
3  title:Orthophoto & DEM (MNE) issues d'images d...   
4  title:Orthophoto & DEM (MNE) issues d'images d...   

                                         Description  \
0  abstract:"Ce jeu de données présente les résul...   
1  abstract:"Ce jeu de données présente les résul...   
2  abstract:"Ce jeu de données présente les résul...   
3  abstract:"Ce jeu de données présente les résul...   
4  abstract:"Ce jeu de données présente les résul...   

                                             Subject  \
0  theme[General]:Madagascar,drone,lagon,lagoon,c...   
1  theme[General]:Madagascar,drone,lagon,lagoon,c...   
2  theme[General]:Madagascar,drone,lagon,lagoon,c...   
3  theme[General]:Madagascar,drone,lagon,lagoon,c...   
4  theme[General]:Madagascar,drone,lagon,lagoon,c...   

                                             Creator  \
0  author:sylvain.poulain@ird.fr,julien.barde@ird...   
1  author:sylvain.poulain@ird.fr,julien.barde@ird...   
2  author:sylvain.poulain@ird.fr,julien.barde@ird...   
3  author:sylvain.poulain@ird.fr,julien.barde@ird...   
4  author:sylvain.poulain@ird.fr,julien.barde@ird...   

                                          Date     Type Language  \
0  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
1  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
2  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
3  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
4  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2023-05-05 13-10-25 - 2023-05-05 13-25-59   
1              NaN  2023-05-04 10-29-18 - 2023-05-04 11-04-15   
2              NaN  2023-09-17 08-42-17 - 2023-09-17 08-55-11   
3              NaN  2023-04-30 13-21-54 - 2023-04-30 13-39-27   
4              NaN  2023-05-02 17-46-21 - 2023-05-02 17-54-30   

                                            Relation  \
0  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
1  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
2  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
3  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
4  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   

                                              Rights  \
0  useLimitation:Utilisation libre sous réserve d...   
1  useLimitation:Utilisation libre sous réserve d...   
2  useLimitation:Utilisation libre sous réserve d...   
3  useLimitation:Utilisation libre sous réserve d...   
4  useLimitation:Utilisation libre sous réserve d...   

                                          Provenance  \
0  statement:"- Camera model and parameters:\n Ma...   
1  statement:"- Camera model and parameters:\n Ma...   
2  statement:"- Camera model and parameters:\n Ma...   
3  statement:"- Camera model and parameters:\n Ma...   
4  statement:"- Camera model and parameters:\n Ma...   

                                              Format  \
0  resource:image/tiff_\ndistribution:image/tiff[...   
1  resource:image/tiff_\ndistribution:image/tiff[...   
2  resource:image/tiff_\ndistribution:image/tiff[...   
3  resource:image/tiff_\ndistribution:image/tiff[...   
4  resource:image/tiff_\ndistribution:image/tiff[...   

                                                Data  
0  source:000_photogrammetry_report.pdf@/home/syl...  
1  source:000_photogrammetry_report.pdf@/home/syl...  
2  source:000_photogrammetry_report.pdf@/hom

In [159]:
data_zip = []
sources = df.iloc[0]['Data'].split('_\n')[0].split(':')[1].split(',')
for data_file in sources:
    data_zip.append(data_file.split('@')[0])

print(data_zip)

['000_photogrammetry_report.pdf', 'PROCESSED_DATA.zip']


In [102]:
### UNZIP PROCESSED_DATA
from zip_helper import *
for entities in range(len(df)):
    print("unzip PROCESSED_DATA.zip in: ", sess_path)
    sess_path = os.path.join(
        input, df.iloc[entities]["Identifier"].split("_\n")[0].split(":")[1]
    )
    try:
        unzip(sess_path, 'PROCESSED_DATA.zip', 'PROCESSED_DATA/PHOTOGRAMMETRY/')
    except:
        print("no_zip in: ", sess_path)
    print("Remove PROCESSED_DATA.zip")
    try:
        os.remove(os.path.join(sess_path, 'PROCESSED_DATA.zip'))
    except:
        print("no_zip to remove in: ", sess_path)
        
    print("Recreate zip")
    zip_folder(os.path.join(sess_path, 'PROCESSED_DATA'), os.path.join(sess_path, 'PROCESSED_DATA'))
    

unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-iot_UAV-02_1
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230505_MDG-sarodrano_UAV-02_2
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230504_MDG-atoll_UAV-02_1
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230917_MDG-nosy-fanhy_UAV-02_1
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230430_MDG-nosyve_UAV-02_3
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-sarodrano_UAV-02_1
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230502_MDG-anakao_UAV-02_1
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /home/sylvain/HDD5To/DATA/MADAGASCAR/20230427_MDG-tulear_UAV-02_1
Remove zip
Recreate zip
unzip PROCESSED_DATA.zip in:  /hom

### Geoflow to upload processed data

In [143]:
# ### Execute geoflow :: upload to geoflow
# # config_raw = os.path.join(output, out_prefix + '_rawfiles-config.json')
# pdata = os.path.join(output, 'comores_processed.json')
# # run_geoflow(config_raw, geoflow_folder)
# os.chdir(geoflow_folder)
# # subprocess.run(["R", "-e", "geoflow::initWorkflow('{}')".format(config_raw)], capture_output=False)
# subprocess.call(["R", "-e", "geoflow::executeWorkflow('{}')".format(pdata)],
#                 stdout=subprocess.DEVNULL, stderr=subprocess.STDOUT,)
# os.chdir(dronemdt_folder)

### Upload processed data with python

In [204]:
### Upload processed_data to Zenodo
print("#### Upload zip files to Zenodo")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url
    
    #### Extract source from Data in dataframe
    data_zip = df.iloc[zipul]['Data'].split('source:')[1].split('_\n')[0]
    if "," in data_zip:
        data_ziptemp = data_zip.split(',')
        data_zip = []
        for dt in range(len(data_ziptemp)):
            data_zip.append(data_ziptemp[dt].split('@')[0])
    else:
        data_zip = data_zip.split('@')[0]
    # data_zip = source_file
    print(data_zip)
    
    
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('\n')[0].split('.')[-1]
        print("DOI already present: ",doi_raw)
        getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        
        if int(doi_raw) == int(getrecid.json()['conceptdoi'].split('.')[-1]) + 1 :
            print("New deposit version")
            newv = zen_newversion(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
            zenval = zenvar(newv)
            print("New doi version:"+zenval[1])

            print("Write DOI to dataframe")
            df.iloc[zipul, df.columns.get_loc('Identifier')] = "id:" + df.iloc[zipul]['Identifier'].split('_\n')[0].split('id:')[1] + "_\ndoi:" + zenval[1]
            
            print("Enrich upload with metadata")
            df.iloc[zipul, df.columns.get_loc("Provenance")] = df.iloc[zipul]["Provenance"] + "_\nprocess:Processed data uploaded to " + base_url.split('api')[0] + "record/" + str(zenval[2])
        
        else:
            print('Version in draft status')
            zenval = zenvar(getrecid)
        
        print("Enrich upload with metadata")
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
        
    else:
        print("Initialize deposit")
        r = check_token(zenodo_baseurl, ACCESS_TOKEN)
        zenval = zenvar(r)
        print("prereserved doi:"+zenval[1])
        print("Write DOI to dataframe")
        dfzen = df
        if 'doi:' in dfzen.iloc[zipul]['Identifier']:
            pass
        else:
            dfzen.iloc[zipul, dfzen.columns.get_loc('Identifier')] = "id:" + dfzen.iloc[zipul]['Identifier'] + "_\ndoi:" + zenval[1]
            dfzen.iloc[zipul, dfzen.columns.get_loc("Provenance")] = dfzen.iloc[zipul]["Provenance"] + "_\nprocess:Processed dataset uploaded to " + base_url.split('api')[0] + "record/" + str(zenval[2])
            
        print("Enrich upload with metadata")
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, zenval[2], df, zipul)
        if zen_metadata.status_code > 400:
            print("error in metadata, please check there is no double keywords: \n" + zen_metadata.text)
            break 

    print("upload data")
    print("    Trying upload number: 1")
    
    for file in data_zip:
        ul_count = 1
        ### Control Filename
        # while file not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
        ### Control md5 checksum:
        ful = os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1], file)
        print(ful)
        with open(ful, "rb") as file_to_check:
            # Open,close, read file and calculate MD5 on its contents 
            # read contents of the file
            ## Python 3.10
            fh = file_to_check.read() 
            # pipe contents of the file through
            digest = hashlib.md5(fh)
            ## End Python 3.10
            # digest = hashlib.file_digest(file_to_check, "md5") ### Python 3.11 only
        print("    md5:", digest.hexdigest())
        while digest.hexdigest() not in zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2])).text:
            #Reset connection every 15 tries
            if ul_count == 15:
                getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
                zenval = zenvar(getrecid)
            
            file_on_server = zenlist_single_files(zenodo_baseurl, ACCESS_TOKEN, str(zenval[2]))
            ### Clean wrong checksum
            if file in file_on_server.text:
                print("    clean wrong files")
                for fs in range(len(file_on_server.json())):
                    if file == file_on_server.json()[fs]['filename']:
                        # print("    sleep 5: computing checksum on server")
                        # time.sleep(15)
                        print("    checksum on server", file_on_server.json()[fs]['checksum'])
                        furl = file_on_server.json()[fs]["links"]["self"]
                        file_to_remove = zen_del_file(furl, ACCESS_TOKEN)
                        
            file_list = [file]            
            zen_upload = zenul(zenval[0], ACCESS_TOKEN, os.path.join(input, df.iloc[zipul]['Identifier'].split('_\n')[0].split(':')[1]), file_list)
            print("        ", zen_upload.text)
            if zen_upload.status_code == 404:
                print("Version doesn't exists ! Please check your record_id")
                break
            else:
                ul_count += 1
                print("    Retry number: " + str(ul_count))
                if zen_upload.status_code == 403:
                    print("        Friday 13th 2023 nightmare => permission denied!")
                    time.sleep(5)    

    ### Publish to Zenodo
    print("Publish record")
    published = zenpublish(zenodo_baseurl, ACCESS_TOKEN, zenval[2])
    print(published.text)

#### Upload zip files to Zenodo

Dataset: 1 / 23 
     id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10079897
['000_photogrammetry_report.pdf', 'PROCESSED_DATA.zip']
DOI already present:  10079897
Version in draft status
Enrich upload with metadata
{'metadata': {'title': "Orthophoto & DEM (MNE) issues d'images drone, UAV, Sarodrano, Madagascar - 20230505 - 02_2", 'publication_date': '2023-10-27', 'description': '"Ce jeu de données présente les résultats des traitements photogrammétriques d’images de drone DJI Mavic 2 Pro UAV acquises sur le site de Sarodrano, Madagascar à la date suivante : 20230505.\n<br />Les vols ont été réalisés en partenariat avec l\'IH.SM dans le but de créer des modèles numériques d\'élévations pour cartographier l\'écosystème marin.\n<br />\n<br /><br />Le paramétrage du logiciel OpenDroneMap est partagé pour permettre la reproductibilité ou l\'amélioration des traitements proposés:<br />\n[\n<br />        {\n<br />            \'name\': \'orthophoto-re

In [198]:
### Check DOI's

for doi in range(len(df)):
    print(df.iloc[doi]["Identifier"])

id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10079897
id:20230504_MDG-atoll_UAV-02_1_
doi:10.5281/zenodo.10079898
id:20230917_MDG-nosy-fanhy_UAV-02_1_
doi:10.5281/zenodo.10079907
id:20230430_MDG-nosyve_UAV-02_3_
doi:10.5281/zenodo.10079908
id:20230502_MDG-sarodrano_UAV-02_1_
doi:10.5281/zenodo.10079911
id:20230502_MDG-anakao_UAV-02_1_
doi:10.5281/zenodo.10079913
id:20230427_MDG-tulear_UAV-02_1_
doi:10.5281/zenodo.10079914
id:20230916_MDG-nosy-sakatia_UAV-02_1_
doi:10.5281/zenodo.10079917
id:20230917_MDG-nosy-fanhy_UAV-02_2_
doi:10.5281/zenodo.10079918
id:20230917_MDG-nosy-fanhy_UAV-02_3_
doi:10.5281/zenodo.10079919
id:20230915_MDG-nosy-sakatia_UAV-02_1_
doi:10.5281/zenodo.10079922
id:20230507_MDG-massif-des-roses_UAV-02_1_
doi:10.5281/zenodo.10079923
id:20230507_MDG-ifaty_UAV-02_1_
doi:10.5281/zenodo.10079924
id:20230912_MDG-nosy-sakatia_UAV-02_1_
doi:10.5281/zenodo.10079929
id:20230504_MDG-saintaugustin_UAV-02_1_
doi:10.5281/zenodo.10079933
id:20230915_MDG-nosy-sakatia_UAV-0

In [197]:
### Export processed data df to csv
# fname = out_prefix + '_zenodo-rawdata'
# df.to_csv(os.path.join(output, fname + ".csv"), quoting=1, quotechar='"', index=False)
df.to_csv(os.path.join(output, out_prefix + "_processed_data_updated_doi.csv"), quoting=1, quotechar='"', index=False)
# # config_raw = os.path.join(output, out_prefix + '_rawfiles-config.json')


### Update RAW Metadata 

In [211]:
# Reload Raw Dataframe
out_prefix = '20231101-161132'
df = {}
df = pd.read_csv(os.path.join(input, out_prefix + '_zenodo-rawdata.csv'))
df.head()

Identifier  \
0  id:20230505_MDG-sarodrano_UAV-02_2_\ndoi:10.52...   
1  id:20230504_MDG-atoll_UAV-02_1_\ndoi:10.5281/z...   
2  id:20230917_MDG-nosy-fanhy_UAV-02_1_\ndoi:10.5...   
3  id:20230430_MDG-nosyve_UAV-02_3_\ndoi:10.5281/...   
4  id:20230502_MDG-sarodrano_UAV-02_1_\ndoi:10.52...   

                                               Title  \
0  title:Images drone UAV, Sarodrano, Madagascar ...   
1  title:Images drone UAV, Atoll, Madagascar - 20...   
2  title:Images drone UAV, Nosy fanhy, Madagascar...   
3  title:Images drone UAV, Nosyve, Madagascar - 2...   
4  title:Images drone UAV, Sarodrano, Madagascar ...   

                                         Description  \
0  abstract:"Jeu de données composé d’images de d...   
1  abstract:"Jeu de données composé d’images de d...   
2  abstract:"Jeu de données composé d’images de d...   
3  abstract:"Jeu de données composé d’images de d...   
4  abstract:"Jeu de données composé d’images de d...   

                                             Subject  \
0  theme[General]:Madagascar,drone,lagon,lagoon,c...   
1  theme[General]:Madagascar,drone,lagon,lagoon,c...   
2  theme[General]:Madagascar,drone,lagon,lagoon,c...   
3  theme[General]:Madagascar,drone,lagon,lagoon,c...   
4  theme[General]:Madagascar,drone,lagon,lagoon,c...   

                                             Creator  \
0  author:sylvain.poulain@ird.fr,julien.barde@ird...   
1  author:sylvain.poulain@ird.fr,julien.barde@ird...   
2  author:sylvain.poulain@ird.fr,julien.barde@ird...   
3  author:sylvain.poulain@ird.fr,julien.barde@ird...   
4  author:sylvain.poulain@ird.fr,julien.barde@ird...   

                                          Date     Type Language  \
0  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
1  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
2  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
3  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
4  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2023-05-05 13-10-25 - 2023-05-05 13-25-59   
1              NaN  2023-05-04 10-29-18 - 2023-05-04 11-04-15   
2              NaN  2023-09-17 08-42-17 - 2023-09-17 08-55-11   
3              NaN  2023-04-30 13-21-54 - 2023-04-30 13-39-27   
4              NaN  2023-05-02 17-46-21 - 2023-05-02 17-54-30   

                                            Relation  \
0  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
1  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
2  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
3  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
4  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   

                                              Rights  \
0  useLimitation:Utilisation libre sous réserve d...   
1  useLimitation:Utilisation libre sous réserve d...   
2  useLimitation:Utilisation libre sous réserve d...   
3  useLimitation:Utilisation libre sous réserve d...   
4  useLimitation:Utilisation libre sous réserve d...   

                                          Provenance  \
0  statement:"- Camera model and parameters:\n Ma...   
1  statement:"- Camera model and parameters:\n Ma...   
2  statement:"- Camera model and parameters:\n Ma...   
3  statement:"- Camera model and parameters:\n Ma...   
4  statement:"- Camera model and parameters:\n Ma...   

                                              Format  \
0  resource:image/jpg_\ndistribution:application/...   
1  resource:image/jpg_\ndistribution:application/...   
2  resource:image/jpg_\ndistribution:application/...   
3  resource:image/jpg_\ndistribution:application/...   
4  resource:image/jpg_\ndistribution:application/...   

                                                Data  
0  source:GPS.zip@/home/sylvain/HDD5To/DATA/MADAG...  
1  source:GPS.zip@/home/sylvain/HDD5To/DATA/MADAG...  
2  source:GPS.zip@/home/sylvain/HDD5To/DATA/

In [216]:
print("##### BEFORE #####\n" + df.iloc[0]["Creator"])
for row in range(len(df)):
    df.iloc[row, df.columns.get_loc("Creator")] = 'author:sylvain.poulain@ird.fr,ainaledon294@gmail.com,a.herinomena11@gmail.com,md.nodc@ihsm.mg,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain.poulain@ird.fr_\npointOfContact:julien.barde@ird.fr_\nprocessor:sylvain.poulain@ird.fr'    

author:sylvain.poulain@ird.fr,julien.barde@ird.fr_
publisher:sylvain.poulain@ird.fr_
owner:sylvain.poulain@ird.fr_
pointOfContact:julien.barde@ird.fr_
processor:sylvain.poulain@ird.fr


In [217]:
print("##### AFTER #####\n" + df.iloc[0]["Creator"])

##### AFTER #####
author:sylvain.poulain@ird.fr,ainaledon294@gmail.com,a.herinomena11@gmail.com,md.nodc@ihsm.mg,julien.barde@ird.fr_
publisher:sylvain.poulain@ird.fr_
owner:sylvain.poulain@ird.fr_
pointOfContact:julien.barde@ird.fr_
processor:sylvain.poulain@ird.fr


In [222]:
### Update Metadata
print("#### Update metadata")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url 
    
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('_\n')[0].split('.')[-1]
        # print("\nDOI already present: ",doi_raw)
        # getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        # print(getrecid.text)
        
        # zenval = zenvar(getrecid)
        # print(zenval)
        # print("\nEnrich upload with metadata")
        zenedit(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, doi_raw, df, zipul, contact_file="/home/sylvain/DroneMDT/geoflow_g2oi_contacts.csv")
        print(zen_metadata)

    ### Publish to Zenodo
    print("Publish record")
    published = zenpublish(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
    print(published.text)

#### Update metadata

Dataset: 1 / 23 
     id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10064364
Using contact file
  Looking for sylvain.poulain@ird.fr
    Look for email sylvain.poulain@ird.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for ainaledon294@gmail.com
    Look for email ainaledon294@gmail.com in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for a.herinomena11@gmail.com
    Look for email a.herinomena11@gmail.com in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for md.nodc@ihsm.mg
    Look for email md.nodc@ihsm.mg in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for julien.barde@ird.fr
    Look for email julien.barde@ird.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
{'metadata': {'title': 'Images drone UAV, Sarodrano, Madagascar - 20230505 - 02_2', 'publication_date': '2

### Update PROCESSED Metadata 

In [223]:
# Reload Raw Dataframe
ouprefix = '20231101-161132'
df = {}
df = pd.read_csv(os.path.join(input, out_prefix + '_processed_data_updated_doi.csv'))
df.head()

Identifier  \
0  id:20230505_MDG-sarodrano_UAV-02_2_\ndoi:10.52...   
1  id:20230504_MDG-atoll_UAV-02_1_\ndoi:10.5281/z...   
2  id:20230917_MDG-nosy-fanhy_UAV-02_1_\ndoi:10.5...   
3  id:20230430_MDG-nosyve_UAV-02_3_\ndoi:10.5281/...   
4  id:20230502_MDG-sarodrano_UAV-02_1_\ndoi:10.52...   

                                               Title  \
0  title:Orthophoto & DEM (MNE) issues d'images d...   
1  title:Orthophoto & DEM (MNE) issues d'images d...   
2  title:Orthophoto & DEM (MNE) issues d'images d...   
3  title:Orthophoto & DEM (MNE) issues d'images d...   
4  title:Orthophoto & DEM (MNE) issues d'images d...   

                                         Description  \
0  abstract:"Ce jeu de données présente les résul...   
1  abstract:"Ce jeu de données présente les résul...   
2  abstract:"Ce jeu de données présente les résul...   
3  abstract:"Ce jeu de données présente les résul...   
4  abstract:"Ce jeu de données présente les résul...   

                                             Subject  \
0  theme[General]:Madagascar,drone,lagon,lagoon,c...   
1  theme[General]:Madagascar,drone,lagon,lagoon,c...   
2  theme[General]:Madagascar,drone,lagon,lagoon,c...   
3  theme[General]:Madagascar,drone,lagon,lagoon,c...   
4  theme[General]:Madagascar,drone,lagon,lagoon,c...   

                                             Creator  \
0  author:sylvain.poulain@ird.fr,julien.barde@ird...   
1  author:sylvain.poulain@ird.fr,julien.barde@ird...   
2  author:sylvain.poulain@ird.fr,julien.barde@ird...   
3  author:sylvain.poulain@ird.fr,julien.barde@ird...   
4  author:sylvain.poulain@ird.fr,julien.barde@ird...   

                                          Date     Type Language  \
0  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
1  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
2  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
3  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   
4  publication:2023-10-27_\nedition:2023-10-27  dataset      fra   

   SpatialCoverage                           TemporalCoverage  \
0              NaN  2023-05-05 13-10-25 - 2023-05-05 13-25-59   
1              NaN  2023-05-04 10-29-18 - 2023-05-04 11-04-15   
2              NaN  2023-09-17 08-42-17 - 2023-09-17 08-55-11   
3              NaN  2023-04-30 13-21-54 - 2023-04-30 13-39-27   
4              NaN  2023-05-02 17-46-21 - 2023-05-02 17-54-30   

                                            Relation  \
0  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
1  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
2  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
3  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   
4  thumbnail:G2OI@https://g2oi.ird.fr/static/img/...   

                                              Rights  \
0  useLimitation:Utilisation libre sous réserve d...   
1  useLimitation:Utilisation libre sous réserve d...   
2  useLimitation:Utilisation libre sous réserve d...   
3  useLimitation:Utilisation libre sous réserve d...   
4  useLimitation:Utilisation libre sous réserve d...   

                                          Provenance  \
0  statement:"- Camera model and parameters:\n Ma...   
1  statement:"- Camera model and parameters:\n Ma...   
2  statement:"- Camera model and parameters:\n Ma...   
3  statement:"- Camera model and parameters:\n Ma...   
4  statement:"- Camera model and parameters:\n Ma...   

                                              Format  \
0  resource:image/tiff_\ndistribution:image/tiff[...   
1  resource:image/tiff_\ndistribution:image/tiff[...   
2  resource:image/tiff_\ndistribution:image/tiff[...   
3  resource:image/tiff_\ndistribution:image/tiff[...   
4  resource:image/tiff_\ndistribution:image/tiff[...   

                                                Data  
0  source:000_photogrammetry_report.pdf@/home/syl...  
1  source:000_photogrammetry_report.pdf@/home/syl...  
2  source:000_photogrammetry_report.pdf@/hom

Modify some authors

In [224]:
for row in range(len(df)):
    df.iloc[row, df.columns.get_loc("Creator")] = 'author:sylvain.poulain@ird.fr,ainaledon294@gmail.com,a.herinomena11@gmail.com,md.nodc@ihsm.mg,julien.barde@ird.fr_\npublisher:sylvain.poulain@ird.fr_\nowner:sylvain.poulain@ird.fr_\npointOfContact:julien.barde@ird.fr_\nprocessor:sylvain.poulain@ird.fr'    

In [225]:
### Update Metadata
print("#### Update metadata")
base_url = "https://zenodo.org/api/"
for zipul in range(len(df)):
    print('\nDataset:', zipul+1, "/" ,len(df), "\n    ",df.iloc[zipul]['Identifier'])
    zenodo_baseurl = base_url 
    
    if 'doi:' in df.iloc[zipul]['Identifier']:
        doi_raw = df.iloc[zipul]['Identifier'].split('_\ndoi:')[1].split('_\n')[0].split('.')[-1]
        # print("\nDOI already present: ",doi_raw)
        # getrecid = zenlist_single(zenodo_baseurl, ACCESS_TOKEN, str(doi_raw))
        # print(getrecid.text)
        
        # zenval = zenvar(getrecid)
        # print(zenval)
        # print("\nEnrich upload with metadata")
        zenedit(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
        zen_metadata = zenmdt(zenodo_baseurl, ACCESS_TOKEN, doi_raw, df, zipul, contact_file="/home/sylvain/DroneMDT/geoflow_g2oi_contacts.csv")
        print(zen_metadata)

    ### Publish to Zenodo
    print("Publish record")
    published = zenpublish(zenodo_baseurl, ACCESS_TOKEN, doi_raw)
    print(published.text)

#### Update metadata

Dataset: 1 / 23 
     id:20230505_MDG-sarodrano_UAV-02_2_
doi:10.5281/zenodo.10079897
Using contact file
  Looking for sylvain.poulain@ird.fr
    Look for email sylvain.poulain@ird.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for ainaledon294@gmail.com
    Look for email ainaledon294@gmail.com in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
  Looking for a.herinomena11@gmail.com
    Look for email a.herinomena11@gmail.com in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for md.nodc@ihsm.mg
    Look for email md.nodc@ihsm.mg in Contact file
      Add First and Last Name
      Add Affiliation
  Looking for julien.barde@ird.fr
    Look for email julien.barde@ird.fr in Contact file
      Add orcid
      Add First and Last Name
      Add Affiliation
{'metadata': {'title': "Orthophoto & DEM (MNE) issues d'images drone, UAV, Sarodrano, Madagascar - 2023050

end